sprawdzamy po kolei czy dziala symulacja i czy zwraca sensowne wyniki

In [1]:
from pathlib import Path
import sys

project_root = Path.cwd().resolve()
if not (project_root / "pipeline").exists():
    for parent in project_root.parents:
        if (parent / "pipeline").exists():
            project_root = parent
            break
sys.path.insert(0, str(project_root))

from pipeline.shared.generate_physical_constants import (
    PHYSICAL_CONSTANTS_CSV_PATH,
    write_physical_constants_csv,
)
from pipeline.exp1.runner.generate_simulation_parameters_csv import (
    write_simulation_parameters_csv,
)
absolute_zero = 273.15


In [2]:
write_physical_constants_csv(PHYSICAL_CONSTANTS_CSV_PATH)
csv_path = write_simulation_parameters_csv(
    temp_initial=absolute_zero + 16.0,
    time_steps=100000,
    time_step=0.5,
    space_step=0.05,
    room_length=5.0,
    room_width=4.0,
    temp_external=absolute_zero + 5.0,
    radiator_size_x=1.0,
    radiator_size_y=0.5,
    radiator_pos_x=0.5,
    radiator_pos_y=0.5,
    window_pos_x=3.0,
    window_width=1.0,
    use_iterative_solver=True
)

import csv

rows = []
with csv_path.open(newline="", encoding="utf-8") as csv_file:
    reader = csv.DictReader(csv_file)
    fieldnames = reader.fieldnames
    for row in reader:
        rows.append(row)

if fieldnames is None:
    raise RuntimeError("Missing CSV header")

if not any(row["name"].strip() == "comfort_temp" for row in rows):
    rows.append(
        {
            "name": "comfort_temp",
            "value": absolute_zero + 21.0,
            "units": "K",
            "description": "Comfort temperature",
        }
    )
    with csv_path.open("w", newline="", encoding="utf-8") as csv_file:
        writer = csv.DictWriter(csv_file, fieldnames=fieldnames)
        writer.writeheader()
        writer.writerows(rows)


Physical constants CSV saved to /home/miplock/Pulpit/laby/modelowanie_deterministyczne/projekt_eksperyment/data/shared/raw/physical_constants.csv
Simulation parameters CSV saved to /home/miplock/Pulpit/laby/modelowanie_deterministyczne/projekt_eksperyment/data/Q1/raw/sim1_params_def.csv


In [3]:
from pipeline.exp1.runner.simulation import run_simulation

run_simulation(progress=True)

Loading physical constants from /home/miplock/Pulpit/laby/modelowanie_deterministyczne/projekt_eksperyment/data/shared/raw/physical_constants.csv...
Loading simulation parameters from /home/miplock/Pulpit/laby/modelowanie_deterministyczne/projekt_eksperyment/data/Q1/raw/sim1_params_def.csv...
Initializing solver...
Running solver and saving results to /home/miplock/Pulpit/laby/modelowanie_deterministyczne/projekt_eksperyment/data/shared/processed/heat_results.pkl...
[==============================] 100000/100000 | sim 13h 53min 20s | ETA 00h 00min 00s
Done.


In [4]:
from pipeline.exp1.plots.plot_heatmap import create_heatmap_figure
from pipeline.exp1.plots.save_heatmap_pkl import _project_root

project_root = _project_root()
pkl_path = project_root / "data/shared/processed/heat_results.pkl"
params_path = project_root / "data/Q1/raw/sim1_params_def.csv"
fig_path = project_root / "data/Q1/figures/heatmap_last.pkl"

fig = create_heatmap_figure(pkl_path, params_path)
fig_path.parent.mkdir(parents=True, exist_ok=True)
import pickle
with fig_path.open("wb") as f:
    pickle.dump(fig, f, protocol=pickle.HIGHEST_PROTOCOL)
fig_path


PosixPath('/home/miplock/Pulpit/laby/modelowanie_deterministyczne/projekt_eksperyment/data/Q1/figures/heatmap_last.pkl')

In [5]:
import pickle
from pipeline.exp1.plots.save_heatmap_pkl import _project_root

project_root = _project_root()
fig_path = project_root / "data/Q1/figures/heatmap_last.pkl"
with fig_path.open("rb") as f:
    fig = pickle.load(f)
fig
